# Projekt munka

1. lépés:
Kaggle regisztráció: https://www.kaggle.com

2. lépés:
Csatlakozás a versenyhez: https://www.kaggle.com/t/b0fc1fc485b146a2887ab6ab8b71c2a8

3. lépés:
Api kulcs generálása (my account-> create new API token), és feltöltése

In [ ]:
!mkdir ~/.kaggle
!mv kaggle.json ~/.kaggle/kaggle.json
!sudo pip3 install kaggle

# Adat letöltése

In [ ]:
import kaggle

kaggle.api.authenticate()

!kaggle competitions download -c artificial-neural-networks-and-their-applications

In [ ]:
!mkdir project

!mv *.tar.gz project/

%cd project

!ls .

!tar -xzf train.tar.gz
!tar -xzf test_images.tar.gz

%cd ..



## Tanító adat betöltése
Az osztály neve az alkönyvtár neve, a képeket pedig matplotlib segítségével olvassuk be.

In [ ]:
import os
import numpy as np
from matplotlib.image import imread

train_x = np.zeros((100000,64*64*3))
train_y = np.array([])
class_id = 0
idx = 0
class_mapping = {}
for category in os.listdir("project/train"):
    print(category)
    
    for img in os.listdir("project/train/"+category+"/images"):
        image = imread("project/train/"+category+"/images/"+img)
        image_n = np.float32(image/255.0) # normalize the image
        
        #handle grayscale images
        if len(image.shape) ==2:
            #print(img, image.shape)
            image_n = np.zeros((64,64,3))
            for i in range(3):
                image_n[:,:,i] = np.float32(image/255.0)
        #flatten the image
        train_x[idx,:] =  np.reshape(image_n, [1,64*64*3])
        idx += 1
        train_y = np.append(train_y, class_id)
    class_mapping[class_id] = category
    class_id += 1

In [ ]:
print(train_x.shape, train_y.shape)
import tensorflow as tf

tf.test.is_gpu_available()

## Neuronháló tanítása

In [ ]:
import tensorflow as tf


# Parameters
learning_rate = 0.01
batch_size = 128
num_steps = train_x.shape[0]/batch_size*10 #10 epoch
display_step = 100

# Network Parameters
n_hidden_1 = 256 # 1st layer number of neurons
n_hidden_2 = 256 # 2nd layer number of neurons
num_input = 64*64*3 # MNIST data input (img shape: 28*28)
num_classes = 200 # MNIST total classes (0-9 digits)

# Define the input function for training
input_fn = tf.estimator.inputs.numpy_input_fn(
    x={'images': train_x}, y=train_y,
    batch_size=batch_size, num_epochs=None, shuffle=True)


# Define the neural network
def neural_net(x_dict):
    # TF Estimator input is a dict, in case of multiple inputs
    x = x_dict['images']
    # Hidden fully connected layer with 256 neurons
    layer_1 = tf.layers.dense(x, n_hidden_1)
    # Hidden fully connected layer with 256 neurons
    layer_2 = tf.layers.dense(layer_1, n_hidden_2)
    # Output fully connected layer with a neuron for each class
    out_layer = tf.layers.dense(layer_2, num_classes)
    return out_layer

# Define the model function (following TF Estimator Template)
def model_fn(features, labels, mode):
    
    # Build the neural network
    logits = neural_net(features)
    
    # Predictions
    pred_classes = tf.argmax(logits, axis=1)
    pred_probas = tf.nn.softmax(logits)
    
    # If prediction mode, early return
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode, predictions=pred_classes) 
        
    # Define loss and optimizer
    loss_op = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits=logits, labels=tf.cast(labels, dtype=tf.int32)))
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
    train_op = optimizer.minimize(loss_op, global_step=tf.train.get_global_step())
    
    # Evaluate the accuracy of the model
    acc_op = tf.metrics.accuracy(labels=labels, predictions=pred_classes)
    
    # TF Estimators requires to return a EstimatorSpec, that specify
    # the different ops for training, evaluating, ...
    estim_specs = tf.estimator.EstimatorSpec(
      mode=mode,
      predictions=pred_classes,
      loss=loss_op,
      train_op=train_op,
      eval_metric_ops={'accuracy': acc_op})

    return estim_specs

# Build the Estimator
model = tf.estimator.Estimator(model_fn)

# Train the Model
model.train(input_fn, steps=num_steps)

## Test halmaz beolvasása

In [ ]:
test_x = np.zeros((10000,64*64*3))
test_filenames = []
idx = 0
for img in os.listdir("project/test_images"):
    image = imread("project/test_images/"+img)
    image_n = np.float32(image/255.0) # normalize the image
    test_filenames.append(img)    
    #handle grayscale images
    if len(image.shape) ==2:
        #print(img, image.shape)
        image_n = np.zeros((64,64,3))
        for i in range(3):
            image_n[:,:,i] = np.float32(image/255.0)
    #flatten the image
    train_x[idx,:] =  np.reshape(image_n, [1,64*64*3])
    idx += 1
print(test_x.shape)

## Predikció

In [ ]:
input_fn_test = tf.estimator.inputs.numpy_input_fn(
    x={'images': test_x},
    batch_size=batch_size, shuffle=False)

preds = list(model.predict(input_fn_test))

f = open('submission.csv', 'w')
f.write('Id,Category\n') # write header
for idx, pred_label in enumerate(preds):
    f.write('%s,%s\n' % (test_filenames[idx], class_mapping[pred_label]))
    
f.close()

**Ne feletsük el feltölteni a predikciós fájlt!**